In [16]:
# Dependencies and Setup
import pandas as pd
import requests
import gmaps

import sys
sys.path.append('/Users/khagenkadariya/World_Weather_Analysis/')
import config

# Import API key
from config import g_key

# Configure gmaps API key
gmaps.configure(api_key=g_key)

In [17]:
# 1. Import the WeatherPy_database.csv file. 
city_data_df = pd.read_csv("../Weather_Database/WeatherPy_database.csv")
city_data_df.head()

Unnamed: 0          City Country      Lat       Lng  Max Temp  Humidity  \
0           0  Port Hedland      AU -20.3167  118.5667    118.45         7   
1           1       Ushuaia      AR -54.8000  -68.3000     36.57        87   
2           2      Hermanus      ZA -34.4187   19.2345     68.90        82   
3           3       Cayambe      EC   0.0500  -78.1333     49.26        96   
4           4      Belmonte      BR -15.8631  -38.8828     75.70        85   

   Cloudiness  Wind Speed Current Description  
0          91       13.80     overcast clouds  
1          50        2.51    scattered clouds  
2         100       17.00     overcast clouds  
3         100        2.75          light rain  
4           5        4.03           clear sky

In [3]:
# 2. Prompt the user to enter minimum and maximum temperature criteria 
# Ask the customer to add a minimum and maximum temperature value.
min_temp = float(input("What is the minimum temperature you would like for your trip?")) 
max_temp = float(input("What is the maximum temperature you would like for your trip?"))

What is the minimum temperature you would like for your trip?65
What is the maximum temperature you would like for your trip?85


In [4]:
# 3. Filter the city_data_df DataFrame using the input statements to create a new DataFrame using the loc method.
# filter the dataset to find the cities that fit the criteria.
preferred_cities_df = city_data_df.loc[(city_data_df["Max Temp"] <= max_temp)&\
                                        (city_data_df["Max Temp"] >= min_temp)]
preferred_cities_df.head(10)

Unnamed: 0       City Country      Lat       Lng  Max Temp  Humidity  \
0            0    Wanning      CN  18.8003  110.3967     67.96        86   
3            3    Samarai      PG -10.6167  150.6667     84.25        72   
5            5     Atuona      PF  -9.8000 -139.0333     78.26        78   
7            7   Upington      ZA -28.4478   21.2561     68.38        68   
8            8   Hermanus      ZA -34.4187   19.2345     66.90        82   
11          11      Kapaa      US  22.0752 -159.3190     75.18        81   
21          21   Kalmunai      LK   7.4167   81.8167     81.16        78   
22          22  Esperance      AU -33.8667  121.9000     72.73        54   
23          23  Thinadhoo      MV   0.5333   72.9333     83.07        70   
26          26     Teknaf      BD  20.8624   92.3058     77.07        45   

    Cloudiness  Wind Speed Current Description  
0           92       10.47     overcast clouds  
3          100       11.41     overcast clouds  
5           22       15.55          light rain  
7           35       10.36    scattered clouds  
8           74        9.15       broken clouds  
11           0        4.61           clear sky  
21          84        8.52       broken clouds  
22          88       16.06     overcast clouds  
23          65       13.67       broken clouds  
26          96        1.16     overcast clouds

In [5]:
# 4a. Determine if there are any empty rows.
preferred_cities_df.count()

Unnamed: 0             248
City                   248
Country                244
Lat                    248
Lng                    248
Max Temp               248
Humidity               248
Cloudiness             248
Wind Speed             248
Current Description    248
dtype: int64

In [6]:
# 4b. Drop any empty rows and create a new DataFrame that doesn’t have empty rows.
preferred_cities_df.isnull().sum()

Unnamed: 0             0
City                   0
Country                4
Lat                    0
Lng                    0
Max Temp               0
Humidity               0
Cloudiness             0
Wind Speed             0
Current Description    0
dtype: int64

In [7]:
# 5a. Create DataFrame called hotel_df to store hotel names along with city, country, max temp, and coordinates.
hotel_df = preferred_cities_df[["City", "Country", "Max Temp", "Current Description", "Lat", "Lng"]].copy()

# 5b. Create a new column "Hotel Name"
hotel_df["Hotel Name"] = ""
hotel_df.head(10)

City Country  Max Temp Current Description      Lat       Lng  \
0     Wanning      CN     67.96     overcast clouds  18.8003  110.3967   
3     Samarai      PG     84.25     overcast clouds -10.6167  150.6667   
5      Atuona      PF     78.26          light rain  -9.8000 -139.0333   
7    Upington      ZA     68.38    scattered clouds -28.4478   21.2561   
8    Hermanus      ZA     66.90       broken clouds -34.4187   19.2345   
11      Kapaa      US     75.18           clear sky  22.0752 -159.3190   
21   Kalmunai      LK     81.16       broken clouds   7.4167   81.8167   
22  Esperance      AU     72.73     overcast clouds -33.8667  121.9000   
23  Thinadhoo      MV     83.07       broken clouds   0.5333   72.9333   
26     Teknaf      BD     77.07     overcast clouds  20.8624   92.3058   

   Hotel Name  
0              
3              
5              
7              
8              
11             
21             
22             
23             
26

In [8]:
# 6a. Set parameters to search for hotels with 5000 meters.
params = {
    "radius": 5000,
    "type": "lodging",
    "key": g_key
}

# Iterate through the DataFrame.
for index, row in hotel_df.iterrows():
    # Get the latitude and longitude.
    lat = row["Lat"]
    lng = row["Lng"]

    # Add the latitude and longitude to location key for the params dictionary.
    params["location"] = f"{lat},{lng}"

    # Use the search term: "lodging" and our latitude and longitude.
    base_url = "https://maps.googleapis.com/maps/api/place/nearbysearch/json"
    # Make request and get the JSON data from the search.
    hotels = requests.get(base_url, params=params).json()
    print(hotels)
  # Grab the first hotel from the results and store the name.
    try:
        hotel_df.loc[index, "Hotel Name"] = hotels["results"][0]["name"]
    except (IndexError):
        print("Hotel not found... skipping.")

{'html_attributions': [], 'next_page_token': 'Aap_uEBApCjdSKlMSt1ep5XRsM-2HA1cwutwyERYU7hUExjY-Dlge_-AkJy6OyKMHl-v7tuKF-NHx4umVAnNtMYch0o7YZUEoDOFhq1B4CPqI9_19Ebt0wIgdwcPHQ3kvDl9byjkFzakOXxpKxXSr2dgPX7X0vcbMGJ9mXeWWulQxZLkPY8DSn3civDRFtFzHLeeE_sAQTRV2cFqiHPs0vs3qF8VJPzUcEP0HrnxBjaE5JQ7CpVFGZIhsFsRm3LBygaCuoXvZt4cIC-P7RLbViEQdQSg8SP07Cb7wDe34Wiw19EnGaJ2m-iOYbH-5d-lpbnc_6yGQv3SPfkg22kUh3Hx9lyiE8Fu6GQYEyvDwdxd6OThDJuFjdVmxWappRs1JRVBpCCQKZzVdBAhm4AfM97eN2hFqa_m_g1Xe-jegBEyc-o6ZDSQ-kpc_Tvw', 'results': [{'business_status': 'OPERATIONAL', 'geometry': {'location': {'lat': 18.796556, 'lng': 110.384287}, 'viewport': {'northeast': {'lat': 18.7980130302915, 'lng': 110.3856020802915}, 'southwest': {'lat': 18.7953150697085, 'lng': 110.3829041197085}}}, 'icon': 'https://maps.gstatic.com/mapfiles/place_api/icons/v1/png_71/lodging-71.png', 'icon_background_color': '#909CE1', 'icon_mask_base_uri': 'https://maps.gstatic.com/mapfiles/place_api/icons/v2/hotel_pinlet', 'name': 'Paradise Hotel', 'place_id'

{'html_attributions': [], 'results': [{'business_status': 'OPERATIONAL', 'geometry': {'location': {'lat': -10.6258967, 'lng': 150.6450828}, 'viewport': {'northeast': {'lat': -10.6245477197085, 'lng': 150.6464317802915}, 'southwest': {'lat': -10.6272456802915, 'lng': 150.6437338197085}}}, 'icon': 'https://maps.gstatic.com/mapfiles/place_api/icons/v1/png_71/lodging-71.png', 'icon_background_color': '#909CE1', 'icon_mask_base_uri': 'https://maps.gstatic.com/mapfiles/place_api/icons/v2/hotel_pinlet', 'name': 'Nuli Sapi', 'place_id': 'ChIJrebljQDVGGkRDM41vUpbU30', 'plus_code': {'compound_code': '9JFW+J2 Kasabanalua, Papua New Guinea', 'global_code': '5RXG9JFW+J2'}, 'rating': 5, 'reference': 'ChIJrebljQDVGGkRDM41vUpbU30', 'scope': 'GOOGLE', 'types': ['lodging', 'point_of_interest', 'establishment'], 'user_ratings_total': 2, 'vicinity': 'Rogeia Island'}], 'status': 'OK'}
{'html_attributions': [], 'results': [{'business_status': 'OPERATIONAL', 'geometry': {'location': {'lat': -9.7952289, 'lng'

{'html_attributions': [], 'next_page_token': 'Aap_uED8VjB05SP7ehnrcE8nq2HVj3dcz0mDjVDahW5PqKSnuRnsjEzh1UofWu6npD3VsY1-ZOxgj9_MEiH3xMXIfAbJpUVgeEheku2CZX4XiVRqkov8skbBDugwX32T-OBcSSMqa6tCbpKeTJdULVhNdGWpz-yNpdXSNBXXmWoQT-Rk0is8cDdVFewGLJ7xkMNRh4gfGnxDKTjFY_64bk65vWQmKrTprB7oPSBdF133x1jivDpTBetvM7_9e6TeaVXhe6mTCPoGem1rp128evmd3uWhAwoqzLl-cCe1LCsAbU6qAzVM1Nvw_-rHM4brUljruPF9SHlhuDuNni22rITksBlnWTPEs-BUYKHmh96h10cA4nr5gpbymFgNewbSBBmlMDLJlwx7OBTLBC4YrVqp93FFWyTsokZLg-qAGunvcIVRoqxF2kQWkDNo', 'results': [{'business_status': 'OPERATIONAL', 'geometry': {'location': {'lat': -28.4497392, 'lng': 21.2638845}, 'viewport': {'northeast': {'lat': -28.44823861970849, 'lng': 21.2651524802915}, 'southwest': {'lat': -28.4509365802915, 'lng': 21.2624545197085}}}, 'icon': 'https://maps.gstatic.com/mapfiles/place_api/icons/v1/png_71/lodging-71.png', 'icon_background_color': '#909CE1', 'icon_mask_base_uri': 'https://maps.gstatic.com/mapfiles/place_api/icons/v2/hotel_pinlet', 'name': 'River Place Manor', 'ope

{'html_attributions': [], 'next_page_token': 'Aap_uEBPds1xI5iiLBlzh11We1arEbEWmsOgc-JImAEjEvM7KH-HbyxI5J9sTJ5DfUkO1DpGpMG3xF6IOH7qffnmtn49QnuM1hfR3c_scvTiqWWud8qa6kn9XVQl0ma6vsQqLDZsxciyGgDFoA6n7RPW2fgIGEm6Ov4VmYpESxOAEXr1-8fFvf745C0ViSMYkBz4_IbI0WKEUGBjMAmVY559PBxi1zSwk6q-6SJte-Fwsg6GBDTq51KVErGEE8UJvbEOTd7lgHxwXY4mQxQp0vjGWWIE52kqGZVlLj1Z6Gs8p4h-bklvIKNe0CPFsi5ZROcUetYZzVUrtFhe05lLf3LO5Th40DWmfBtxKSY2FAgUN6tIk7GJzWtBYPvL4N_NJBg_HwgqiAf4sPNmmH204OCxzT68MxqDEfYW-m5mtvynOMXHe0sT89AmCYna', 'results': [{'business_status': 'OPERATIONAL', 'geometry': {'location': {'lat': -34.4213898, 'lng': 19.2366413}, 'viewport': {'northeast': {'lat': -34.4200678697085, 'lng': 19.2380084302915}, 'southwest': {'lat': -34.4227658302915, 'lng': 19.2353104697085}}}, 'icon': 'https://maps.gstatic.com/mapfiles/place_api/icons/v1/png_71/lodging-71.png', 'icon_background_color': '#909CE1', 'icon_mask_base_uri': 'https://maps.gstatic.com/mapfiles/place_api/icons/v2/hotel_pinlet', 'name': 'Misty Waves Boutique Hote

{'html_attributions': [], 'next_page_token': 'Aap_uECsatcvxe-NiFxpEQITP_DAmPXg8H4fbf35JSaWJ50GwPl9vuYHeDSEci0wQWc9uaW7GMntZUs26UgDSXD7u8nL6__TWgla5em-9jBh90ea6yA6jt7RPJ7Y9neR8qZUML3hSZKIPlM_XGqk95Y0r71OFmkH7akDiygYTssj9piRGibnz-MUYpdunHUk8Ww_-tsHGxuvvDrwaCkpTGx-Op9qaK4N2LsGB9SmblyZMl17q9wJpzMB6ik2MVVb4T3OnLkmBRYaiILZvTzz39Pv1snFKXcXlq1uoMW8cfHUKi3p0wDpAYvwT3xyTUYFZOk-aTn-OpNVe0fKJDBpBC5YMZ9QzJVKO2TdMBf0jp6TjZ8oudyAD1g6OwcZEHptwP-Ng2qNJ9LcQA9ANZQRZ0kLGGlv8r8G0qlkP0K_xVgMe1bsSfcT1Daw-nla', 'results': [{'business_status': 'OPERATIONAL', 'geometry': {'location': {'lat': 22.0567556, 'lng': -159.3225167}, 'viewport': {'northeast': {'lat': 22.0581973802915, 'lng': -159.3212929697085}, 'southwest': {'lat': 22.0554994197085, 'lng': -159.3239909302915}}}, 'icon': 'https://maps.gstatic.com/mapfiles/place_api/icons/v1/png_71/lodging-71.png', 'icon_background_color': '#909CE1', 'icon_mask_base_uri': 'https://maps.gstatic.com/mapfiles/place_api/icons/v2/hotel_pinlet', 'name': 'Sheraton Kauai Coconut

...

{'html_attributions': [], 'results': [{'business_status': 'OPERATIONAL', 'geometry': {'location': {'lat': -14.4068741, 'lng': -56.4387222}, 'viewport': {'northeast': {'lat': -14.40546286970849, 'lng': -56.4374100697085}, 'southwest': {'lat': -14.4081608302915, 'lng': -56.4401080302915}}}, 'icon': 'https://maps.gstatic.com/mapfiles/place_api/icons/v1/png_71/lodging-71.png', 'icon_background_color': '#909CE1', 'icon_mask_base_uri': 'https://maps.gstatic.com/mapfiles/place_api/icons/v2/hotel_pinlet', 'name': 'Hotel Delta', 'photos': [{'height': 2448, 'html_attributions': ['<a href="https://maps.google.com/maps/contrib/110206499169688139071">Antonio Carlos</a>'], 'photo_reference': 'Aap_uEAVpeRUONRq1uuMHoDp7dOfSYtYK83uLOgNnfMYxydAb6mw6z1YiVMoRkYs_YagnXoPtn2B64cPWYAF8E69S7NPWCMut2L-ja_iMobgS7iVL6mMY0TpQ3SwOGD06Yyai_bolHwuDTn_ZznagpPuOV855VgZ1Z7H5cvOzZwhvEHvy17g', 'width': 3264}], 'place_id': 'ChIJq6qqal8an5MRoZ-BhnuuQsI', 'plus_code': {'compound_code': 'HHV6+7G Diamantino, State of Mato Gro

{'html_attributions': [], 'next_page_token': 'Aap_uEB2YzuDugEsCKMeMR327kiK7UfiZCgdODaAsJ8Wa5zhft5uwzXz8EKPkuj25fVDet8-oThbpsFAeVYyLqbV7EK8qMRT18i4pt2nCrbnO2LV9eEY3ExzKx9r1QxmoXj5qNAAv_yUa0Q-2LXB0Y9vqs_wNRFvIk5ihv31gIs-USopc5Cg2xBkl2X-7p1bMYo48qA9mNMl4i3GZaPMx1rwyUX1qtW51eVOECIwrfQShMCOBDAURD2jEVHDifZcU7H2EtgD_zbZSu4hqXQfQkIC19DQbntV-rhKxRyPRrqMsbf0tAW1UmsEuuTt6eEC6-2VTGu_p8lt_raw5gV00hIHat_hNUL5uGfMlCvcxnck3WKfSXh8j5R9zJvV3UEhgDUdbVRXF9dLnTXwEFMUcC5gP_hORvQVwTX8yfXPG2pnQzg5JrqB_RXI5Ilq', 'results': [{'business_status': 'OPERATIONAL', 'geometry': {'location': {'lat': -2.8530306, 'lng': 108.2879974}, 'viewport': {'northeast': {'lat': -2.851617219708498, 'lng': 108.2893811302915}, 'southwest': {'lat': -2.854315180291501, 'lng': 108.2866831697085}}}, 'icon': 'https://maps.gstatic.com/mapfiles/place_api/icons/v1/png_71/lodging-71.png', 'icon_background_color': '#909CE1', 'icon_mask_base_uri': 'https://maps.gstatic.com/mapfiles/place_api/icons/v2/hotel_pinlet', 'name': 'Guest Hotel', 'photos

{'html_attributions': [], 'next_page_token': 'Aap_uEBWwaNVtUsm0DYwhv02F5DbYeExA0WvWt-qEMfW6FLeKP39oUHgdrlLRsc9PdXQtuIufZbPB0TZYAtOugKv2ZPE1AaXugRoJ_1Fr-8xfQADufDc5mN1C4hAlqNVA6RUkX_hk58Ja-aag6dOZZy7pwOBPqOw7b_gdtTKW4gjGTvsVQXFIHYEI6ivnaLfy-dk9i25yTwsWiC7jXkQ-FCQKWuhAJCntr57UJgHMwcewkCo4koqDxmyMwVK8ghQTDcwZxohcNQ7xkRBgLhymOtGabVNyPoYmjZcr0_BIJetu_d6hD9UgLSwH_kg3ZmxE5MmSun33GjPovSt14HecEuMDJNTz2o6yep0oYCQU6ZrTf-4dKpZFYpe0cj7c3Ink3x6net_7MozfTgocpc19yFtBcCPo93W8FTOSUowNu0sgWnMYCiwRKOjfcc8', 'results': [{'business_status': 'OPERATIONAL', 'geometry': {'location': {'lat': -29.8530769, 'lng': 31.0288269}, 'viewport': {'northeast': {'lat': -29.8518079197085, 'lng': 31.03014853029149}, 'southwest': {'lat': -29.8545058802915, 'lng': 31.0274505697085}}}, 'icon': 'https://maps.gstatic.com/mapfiles/place_api/icons/v1/png_71/lodging-71.png', 'icon_background_color': '#909CE1', 'icon_mask_base_uri': 'https://maps.gstatic.com/mapfiles/place_api/icons/v2/hotel_pinlet', 'name': 'Hilton Durban', 'photos'

{'html_attributions': [], 'results': [{'business_status': 'OPERATIONAL', 'geometry': {'location': {'lat': 3.3733413, 'lng': -59.7953117}, 'viewport': {'northeast': {'lat': 3.374532680291502, 'lng': -59.7938515197085}, 'southwest': {'lat': 3.371834719708498, 'lng': -59.7965494802915}}}, 'icon': 'https://maps.gstatic.com/mapfiles/place_api/icons/v1/png_71/lodging-71.png', 'icon_background_color': '#909CE1', 'icon_mask_base_uri': 'https://maps.gstatic.com/mapfiles/place_api/icons/v2/hotel_pinlet', 'name': 'Savannah Inn', 'photos': [{'height': 4000, 'html_attributions': ['<a href="https://maps.google.com/maps/contrib/106275714991603427076">Steve Yatomi</a>'], 'photo_reference': 'Aap_uEAdUhESA3MQwZbLU3N_6L1MmHpJ0tZWZ8ntpFqgDdNG50QePsdDAE-TTUXGwbmjaq-HHHZ5IyNmQjfT1DvUsq1qIN4CeUU7HwNg_rNmD_IWyzv2WE0-3cw06pj520JZjb2DUSxnXzrNzkb0QUbGWoSl-VVbYzpKAnxottKC0lqcoTvm', 'width': 2250}], 'place_id': 'ChIJKWy8BH6olo0RoCX8Q5yVn3E', 'rating': 3.8, 'reference': 'ChIJKWy8BH6olo0RoCX8Q5yVn3E', 'scope': 'GOOG

{'html_attributions': [], 'next_page_token': 'Aap_uEDK019vUEaCaFy5xaLB5OVKUZNzbiiJoct8EMV2ITPB18yNirPQ6Rfik9eE-onG_Xhru6B7LeQ5XqN96gHKAzyNo2mV4qtf1_KQbW6TJOpAPdNFFXyP9fxT7RoG7672Pw29awfSjoHbUPqkOLllj2kAk20WrHPOUQ5dsmw2cKnINvvlDo9SaoLO6j55M39DxqUBmnL-7GtKcbbvoURzsvwEeD5xcbbh0wl7ocTE9OEKLAiSz_83qWnFUk5JeK2o0Dej9pzFeX8GcBKs3aAQx0zioQb3ualMbs8cdg4fr2ISnUBQwxUuxcNbtj4bzYFt2mCKG5b7gBNYrei0-BpK-GWFCjYqzlGmBbcXSbGnFH2zQpVlrhBctzbSu6wUqB7EfMoi9cd6pQg8mrP3JsNh7IRCIBRTivFDASvuc3PZHMdj2OgDe2l9rTPB', 'results': [{'business_status': 'OPERATIONAL', 'geometry': {'location': {'lat': -44.7007979, 'lng': 169.1153947}, 'viewport': {'northeast': {'lat': -44.69936766970851, 'lng': 169.1169022802915}, 'southwest': {'lat': -44.70206563029151, 'lng': 169.1142043197085}}}, 'icon': 'https://maps.gstatic.com/mapfiles/place_api/icons/v1/png_71/lodging-71.png', 'icon_background_color': '#909CE1', 'icon_mask_base_uri': 'https://maps.gstatic.com/mapfiles/place_api/icons/v2/hotel_pinlet', 'name': 'Wanaka Homestead Lod

In [9]:
hotel_df

City Country  Max Temp Current Description      Lat       Lng  \
0       Wanning      CN     67.96     overcast clouds  18.8003  110.3967   
3       Samarai      PG     84.25     overcast clouds -10.6167  150.6667   
5        Atuona      PF     78.26          light rain  -9.8000 -139.0333   
7      Upington      ZA     68.38    scattered clouds -28.4478   21.2561   
8      Hermanus      ZA     66.90       broken clouds -34.4187   19.2345   
..          ...     ...       ...                 ...      ...       ...   
671  Diamantino      BR     71.15     overcast clouds -14.4086  -56.4461   
673     Manggar      ID     79.14     overcast clouds  -2.8833  108.2667   
677      Durban      ZA     80.02       broken clouds -29.8579   31.0292   
679      Lethem      GY     78.39     overcast clouds   3.3803  -59.7968   
680      Wanaka      NZ     72.48     overcast clouds -44.7000  169.1500   

                              Hotel Name  
0                         Paradise Hotel  
3                              Nuli Sapi  
5                            Villa Enata  
7                      River Place Manor  
8             Misty Waves Boutique Hotel  
..                                   ...  
671                          Hotel Delta  
673                          Guest Hotel  
677                        Hilton Durban  
679                         Savannah Inn  
680  Wanaka Homestead Lodge and Cottages  

[248 rows x 7 columns]

In [10]:
# 8a. Create the output File (CSV)
output_data_file = "data/WeatherPy_vacation.csv"
# 8b. Export the City_Data into a csv
hotel_df.to_csv("../Vacation_Search/WeatherPy_vacation.csv")

In [11]:
# 9. Using the template add city name, the country code, the weather description and maximum temperature for the city.
info_box_template = """
<dl>
<dt>Hotel Name</dt><dd>{Hotel Name}</dd>
<dt>City</dt><dd>{City}</dd>
<dt>Country</dt><dd>{Country}</dd>
<dt>Max Temp</dt><dd>{Max Temp} °F</dd>
</dl>
"""

# 10a. Get the data from each row and add it to the formatting template and store the data in a list.
hotel_info = [info_box_template.format(**row) for index, row in hotel_df.iterrows()]

# 10b. Get the latitude and longitude from each row and store in a new DataFrame.
locations = hotel_df[["Lat", "Lng"]]

In [15]:
# 11a. Add a marker layer for each city to the map. 
# Add a heatmap of temperature for the vacation spots and a pop-up marker for each city.
locations = hotel_df[["Lat", "Lng"]]
max_temp = hotel_df["Max Temp"]
fig = gmaps.figure(center=(30.0, 31.0), zoom_level=1.5)
heat_layer = gmaps.heatmap_layer(locations, weights=max_temp,dissipating=False,
             max_intensity=300, point_radius=4)
marker_layer = gmaps.marker_layer(locations, info_box_content=hotel_info)
fig.add_layer(heat_layer)
fig.add_layer(marker_layer)

# 11b. Display the figure
fig

Figure(layout=FigureLayout(height='420px'))